In [ ]:
import tensorflow as tf
device_name=tf.test.gpu_device_name()
if device_name!='/device:GPU:0':
  raise SystemError ('GPUdevicenotfound')
print('FoundGPUat:{}'.format(device_name))

In [ ]:
#загрузка датасета
from keras.datasets import imdb
vocabulary_size=5000
index_from=3
(X_train,y_train),(X_test,y_test)=imdb.load_data(path="imdb.npz",num_words=vocabulary_size,skip_top=0,maxlen=None,seed=15,start_char=1,oov_char=2,index_from=index_from)

In [ ]:
# Вывод размеров массивов данных
print("Размеры обучающих данных:")
print(f"X_train: {len(X_train)} ")
print(f"y_train: {y_train.shape}")
print("\nРазмеры тестовых данных:")
print(f"X_test: {len(X_test)} ")
print(f"y_test: {y_test.shape}")

In [ ]:
# Пункт 3: Создание словаря для перевода индексов в слова
# Загрузка словаря "слово:индекс"
word_to_id = imdb.get_word_index()

# Уточнение словаря
word_to_id = {key: (value + index_from) for key, value in word_to_id.items()}
word_to_id["<PAD>"] = 0
word_to_id["<START>"] = 1
word_to_id["<UNK>"] = 2
word_to_id["<UNUSED>"] = 3

In [ ]:
# Создание обратного словаря "индекс:слово"
id_to_word = {value: key for key, value in word_to_id.items()}

# Вывод одного отзыва из обучающего множества
import random
sample_index = random.randint(0, len(X_train)-1)
print(f"\nОтзыв №{sample_index}")
print("Список индексов слов:")
print(X_train[sample_index])

In [ ]:
# Преобразование в текст
review_as_text = ' '.join(id_to_word.get(id, '<UNK>') for id in X_train[sample_index])
print("\nОтзыв в виде текста:")
print(review_as_text)

# Длина отзыва и метка класса
print(f"\nДлина отзыва: {len(X_train[sample_index])} слов")
print(f"Метка класса: {y_train[sample_index]} ({'Positive' if y_train[sample_index] == 1 else 'Negative'})")

In [ ]:
# Пункт 4: Максимальная и минимальная длина отзыва в обучающем множестве
lengths = [len(review) for review in X_train]
max_length = max(lengths)
min_length = min(lengths)
print(f"Максимальная длина отзыва: {max_length} слов")
print(f"Минимальная длина отзыва: {min_length} слов")

In [ ]:
# Пункт 5: Предобработка данных
from tensorflow.keras.utils import pad_sequences

max_words = 500  # Выбранная единая длина

X_train = pad_sequences(
    X_train,
    maxlen=max_words,
    value=0,
    padding='pre',
    truncating='post'
)

In [ ]:
X_test = pad_sequences(
    X_test,
    maxlen=max_words,
    value=0,
    padding='pre',
    truncating='post'
)

In [ ]:
# Пункт 6: Повторение п. 4 после предобработки
print(f"Длина всех отзывов: {X_train.shape[1]} слов")


In [ ]:
# Пункт 7: Повторение п. 3 после предобработки
print("Список индексов слов:")
print(X_train[sample_index])


In [ ]:
# Преобразование в текст (игнорируем нулевые паддинги)
review_after_preprocessing = ' '.join(
    id_to_word.get(id, '<UNK>') for id in X_train[sample_index] if id != 0
)
print("\nОтзыв в виде текста после предобработки:")
print(review_after_preprocessing)

print(f"\nДлина отзыва после предобработки: {len([id for id in X_train[sample_index] if id != 0])} значимых слов")
print(f"Общая длина с паддингом: {len(X_train[sample_index])}")

print("\nВывод: После предобработки все отзывы приведены к единой длине 500 слов.")



In [ ]:
# Пункт 8: Вывод предобработанных массивов и их размерностей
print("Предобработанное обучающее множество X_train (первые 5 примеров):")
print(X_train[:5])
print("\nПредобработанное тестовое множество X_test (первые 5 примеров):")
print(X_test[:5])
print(f"Размерность X_train после предобработки: {X_train.shape}")
print(f"Размерность X_test после предобработки: {X_test.shape}")
print(f"Размерность y_train: {y_train.shape}")
print(f"Размерность y_test: {y_test.shape}")

In [ ]:

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, LSTM, Dropout, Dense
import numpy as np

model = Sequential()

model.add(Embedding(
    input_dim=vocabulary_size,
    output_dim=32,
    input_length=max_words
))


model.add(LSTM(units=100))


model.add(Dropout(rate=0.3))


model.add(Dense(1, activation='sigmoid'))  #


model.build(input_shape=(None, max_words))


model.compile(
    loss='binary_crossentropy',
    optimizer='adam',
    metrics=['accuracy']
)


print("Архитектура нейронной сети")
model.summary()

In [ ]:
history = model.fit(
    X_train,
    y_train,
    validation_split=0.2,
    batch_size=64,
    epochs=5,
    verbose=1
)

In [ ]:
# Проверяем достигнутое качество на валидационных данных
val_accuracy = history.history['val_accuracy'][-1]
print(f"\nТочность на валидационных данных: {val_accuracy:.4f}")
if val_accuracy >= 0.8:
    print("Цель достигнута: accuracy >= 0.8")
else:
    print("Цель не достигнута: accuracy < 0.8")

In [ ]:
# Пункт 10: Оценка качества обучения на тестовых данных

# 1) Значение метрики качества классификации на тестовых данных
print("\n1) Метрика качества на тестовых данных:")
test_loss, test_accuracy = model.evaluate(X_test, y_test, verbose=0)
print(f"   Loss: {test_loss:.4f}")
print(f"   Accuracy: {test_accuracy:.4f}")

In [ ]:
# 2) Отчет о качестве классификации тестовой выборки
y_score = model.predict(X_test, verbose=0)

# Преобразуем вероятности в бинарные предсказания (порог 0.5)
y_pred = [1 if y_score[i, 0] >= 0.5 else 0 for i in range(len(y_score))]

from sklearn.metrics import classification_report
print(classification_report(y_test, y_pred, labels=[0,1], target_names=['Negative','Positive']))

In [ ]:
# 3) Построение ROC-кривой и вычисление AUC-ROC
from sklearn.metrics import roc_curve, auc, roc_auc_score
import matplotlib.pyplot as plt

fpr, tpr, thresholds = roc_curve(y_test, y_score)

plt.figure(figsize=(8, 6))
plt.plot(fpr, tpr, color='darkorange', lw=2, label=f'ROC curve (AUC = {auc(fpr, tpr):.4f})')
plt.xlim([0.0, 1.0])
plt.ylim([0.0, 1.05])
plt.xlabel('False Positive Rate')
plt.ylabel('True Positive Rate')
plt.title('ROC Curve')
plt.legend(loc="lower right")
plt.grid(True)
plt.show()

In [ ]:
# Вычисляем AUC-ROC
auc_roc = roc_auc_score(y_test, y_score)
print(f"   Площадь под ROC-кривой (AUC-ROC): {auc_roc:.4f}")